# Introduction

I've always been interested in automatic harmonization because it feels like something kind of natural for humans, especially on simple melodies. Bach Chorales are a nice test set because there's a lot of them, and each instrument has only a monophonic sequence of notes, since they were written for voices. Hadjeres et al did some work on harmonizing Bach Chorales, so this notebook is definitely inspired by their contributions. Let's see what happens!

In [ ]:
import requests
from urllib import request, response, error, parse
from urllib.request import urlopen
from bs4 import BeautifulSoup
import numpy as np
from tqdm.notebook import tqdm
import glob
from itertools import compress
import torch
from torch import nn
from torch.utils import data
import time
import copy
!pip install pypianoroll

     |████████████████████████████████| 5.6MB 4.1MB/s 
     |████████████████████████████████| 61kB 5.5MB/s 
  Created wheel for pypianoroll: filename=pypianoroll-0.5.3-cp36-none-any.whl size=23827 sha256=524f306db9723729c70ebead8c76370a24b43d2e9107809dded1f35456e05e15
  Stored in directory: /root/.cache/pip/wheels/29/c8/c0/7b240ab723c2f96b03391796bdf278de513eabf1dfb989c07f
  Created wheel for pretty-midi: filename=pretty_midi-0.2.9-cp36-none-any.whl size=5591953 sha256=663bc92e86494c65c3e1d4c985600e85dfb4d88671d1b5edc7f0ece71f8071f2
  Stored in directory: /root/.cache/pip/wheels/4c/a1/c6/b5697841db1112c6e5866d75a6b6bf1bef73b874782556ba66
Successfully built pypianoroll pretty-midi


# Data

So I thought Bach Chorales were going to be super accessible, but it's turned out to be way more annoying to find -- the site where a lot of other people got the midis is no longer up, another site required me to pay, and a third didn't have all the chorales. But I did eventually find the files I was looking for in the oddest of all places: a github repo for an unfinished project (sounds familiar). Well, without further ado, let's scrape all the midis from our new friend James Robert Floyd's github!

In [ ]:
def download_midi_chorales(data_dir):
  base_url = 'https://github.com/jamesrobertlloyd/infinite-bach/tree/master/data/chorales/midi'
  html = urlopen(base_url)
  soup = BeautifulSoup(html, "lxml")
  links = soup.find_all('a', class_ ='js-navigation-open link-gray-dark')
  print(len(links))
  for link in tqdm(links):
    song_path = 'https://github.com'+link.attrs['href']
    ext = song_path.split('.')[-1]
    if ext == 'mid':
      song_name = song_path.split('/')[-1]
      # one small change needed to get the actual link, not the gui for the file on github
      song_path = song_path.replace("/blob/", "/raw/")
      with open(data_dir+song_name,'wb') as handle:
        response = requests.get(song_path, stream=True)
        if response.ok:
          handle.write(response.content)

# download_midi_chorales() # we only need to do this once, so I've commented it out

Let's install the package we'll use to manipulate the midi files, 'pretty_midi'.

In [ ]:
!pip install pretty_midi
import pretty_midi

In [ ]:
def find_four_track_chorales():
  cnts = {}
  four_tracks = []
  for song in tqdm(glob.glob(data_dir+'/*')):
    try:
      mid = pretty_midi.PrettyMIDI(song)
      num_instr = len(mid.instruments)
      if num_instr not in cnts.keys():
        cnts[num_instr] = 1
      else:
        cnts[num_instr] += 1

      if num_instr == 4:
        four_tracks.append(song)
    except Exception:
      pass
  print(cnts)
  return four_tracks

Hmm, so not all of these MIDIs are only four voices. I've looked at some of the MIDIs with more than four tracks and it seems to be vocals with some accompaniment. The accompaniment is not monophonic, so I think to just simplify things, I'll only work with the midis that seem to be just four voice chorales. Note that we still retain about 75% of our data (by song count). Nice!

In [ ]:
def remove_polyphony(four_tracks):
  min_pitches = []
  max_pitches = []
  def check_mono(mid):
    mid2 = pretty_midi.PrettyMIDI()
    for instr in mid.instruments:
      mid2.instruments = [instr]
      piano_roll = mid2.get_piano_roll()
      bin_proll = piano_roll
      bin_proll[bin_proll > 0] = 1
      max_notes_per_step = np.max(np.sum(bin_proll, axis=0))
      min_pitches.append(np.min(np.nonzero(bin_proll)[0]))
      max_pitches.append(np.max(np.nonzero(bin_proll)[0]))
      # print(max_notes_per_step)
      if max_notes_per_step > 1:
        print('Failed: ', instr)
        return False
    return True

  isMono = [check_mono(pretty_midi.PrettyMIDI(x)) for x in tqdm(four_tracks)]
  print(min(min_pitches), max(max_pitches))
  four_voices = list(compress(four_tracks, isMono))
  print(len(four_voices))
  print(len(four_tracks))
  return four_voices

I wanted to check through my data once more to confirm that I am working with four voice chorales. Here, we used the intuition that a sequence of notes to be sang must be monophonic (one note per time step). We're now done to 373 chorales. This seems like a tiny dataset, but we'll make it larger by taking shorter segments (potentially overlapping) from each chorale. Also, we see that we can greatly reduce the number of pitches to consider, which makes sense, as a piano has a much larger range than a human voice. I'll use a range from pitch 20 to pitch 90, though our data only has pitches from 24 to 84. 

Let's save this list of four-voice chorales so that I won't have to do the preprocessing everytime I modify/run this notebook.

In [ ]:
data_dir = 'drive/My Drive/deep_learning_fun/harmonization/chorales/'
preprocess = False

if preprocess:
  print('Downloading all chorales to google drive')
  # download_midi_chorales()
  four_tracks = find_four_track_chorales()
  four_voices = remove_polyphony(four_tracks)
  print('Writing list of monophonic chorales to four_voice_chorales.txt')
  with open(data_dir+'four_voice_chorales.txt', 'w') as file:
    file.write('\n'.join(four_voices))

chorales = []
with open(data_dir+'four_voice_chorales.txt', 'r') as file:
  for line in file:
    chorales.append(line[:-1]) # yes this is hacky, but I don't want the \n

print(chorales[:10])

['drive/My Drive/deep_learning_fun/harmonization/chorales/003608b2.mid', 'drive/My Drive/deep_learning_fun/harmonization/chorales/003706b_.mid', 'drive/My Drive/deep_learning_fun/harmonization/chorales/004006b_.mid', 'drive/My Drive/deep_learning_fun/harmonization/chorales/004008b_.mid', 'drive/My Drive/deep_learning_fun/harmonization/chorales/003806b_.mid', 'drive/My Drive/deep_learning_fun/harmonization/chorales/003907b_.mid', 'drive/My Drive/deep_learning_fun/harmonization/chorales/004207b_.mid', 'drive/My Drive/deep_learning_fun/harmonization/chorales/004311b_.mid', 'drive/My Drive/deep_learning_fun/harmonization/chorales/004606bs.mid', 'drive/My Drive/deep_learning_fun/harmonization/chorales/004407b_.mid']


## Split into segments

For our first experiment, let's go with holding out one of the tracks. My plan is to use piano rolls as input and output to the network. I notice that when we get a piano roll using pretty_midi for a multitrack piece, the resulting roll is just the sum of each roll. The issue is that I wouldn't know how to go back from this combined piano roll to the multitrack chorale. A get around will be to binarize the chorales -- they'll sound worse since there won't be any dynamics, but at least the piano roll for one track and multitrack is now identical. 

So what we want is to take each midi and get the piano roll for each instrument. We'll split the piano rolls into some segment length (maybe 8 seconds), and then form four input-output pairs -- each time holding out one of the tracks. 

In [ ]:
def binarize(roll):
  roll[roll > 0] = 1
  return roll

fs = 16


inputs = []
outputs = []
outputs2 = []
seq_len = fs * 6
overlap = 1
for piece in tqdm(chorales):
  try:
    mid = pretty_midi.PrettyMIDI(piece)
    full_roll = mid.get_piano_roll(fs=fs)[20:90,:]
    mid2 = pretty_midi.PrettyMIDI()
    for instr in mid.instruments:
      try:
        mid2.instruments = [instr]
        instr_roll = mid2.get_piano_roll(fs=fs)[20:90,:]
        input = binarize(full_roll - instr_roll)
        output = binarize(full_roll)
        for i in range(0, np.shape(input)[1]-seq_len, int(seq_len // overlap)):
          inputs.append(input[:,i:i+seq_len])
          outputs.append(output[:,i:i+seq_len])
          outputs2.append(binarize(instr_roll[:,i:i+seq_len]))
      except Exception:
        pass
  except Exception:
    chorales.remove(piece)

print(len(inputs))
print(len(outputs))


10474
10474


Finally, let's make appropriate test and train torch datasets. 

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"

In [ ]:
# we'll use an 80/20 split
train_size = int(len(inputs) * 0.8)
# notice that we're not randomizing -- this should make the validation set harder
train_in, train_out = [x[:train_size] for x in [inputs, outputs2]]
val_in, val_out = [x[train_size:] for x in [inputs, outputs2]]
train_i, val_i = [torch.Tensor(i) for i in [train_in, val_in]]
train_o, val_o = [torch.Tensor(o) for o in [train_out, val_out]]
train, test = [data.TensorDataset(i,o) for i,o in [(train_i, train_o), (val_i, val_o)]]
batch_size = 32
train_loader, test_loader = [data.DataLoader(x, batch_size=batch_size, shuffle=True) \
                             for x in [train, test]]

Nice, we have over 10,000 segments. I'm really curious to see if this is going to work! As a recap, we scraped some dude's github to download all the chorales, then filtered them to only keep monophonic four track chorales. Our final preparation was to create input-output pairs where one track was held out for each pair. We clip the piano rolls to only have pitches 20 through 90, and we use 6 seconds as our segment length. 

# Architecture

OK! We have our data all ready to go. Honestly, I have no idea what kind of network I want. One thing that I think would be important is being able to see both local and long term structure, which is crucial in music. Convolutions can pick up local structure, and having multiple consecutive convolutions increase the receptive field. 

Another idea is to try to leverage skip connections like a U-net, particularly because the inputs and outputs are going to be very similar, both in shape and in content (after all, we just want our network to add in one track). 

I think the simplest thing to try first is just a fully connected network. Our data is sparse and if we include one skip connection between the first and last layers, reconstructing the original input will already be taken care of. 

For our loss, we can maybe do an RMS error. In theory, an NLL loss could also work since our data is binary. Perhaps we'll try both.

In [ ]:
class Harmonizer(nn.Module):
  def __init__(self):
    super(Harmonizer, self).__init__()
    # size is 70 * 96 = 6720
    self.fc1 = nn.Linear(6720, 3370)
    self.fc2 = nn.Linear(3370, 1650)
    self.fc3 = nn.Linear(1650, 825)
    self.fc4 = nn.Linear(825, 1650)
    self.fc5 = nn.Linear(1650, 3370)
    self.fc6 = nn.Linear(3370, 6720)
    self.relu = nn.ReLU()
    self.sigmoid = nn.Sigmoid()

  def forward(self, input):
    flat = input.view(input.shape[0], -1)
    h1 = self.relu(self.fc1(flat))
    h2 = self.relu(self.fc2(h1))
    h3 = self.relu(self.fc3(h2))
    h4 = self.relu(self.fc4(h3))
    h5 = self.relu(self.fc5(h4))
    h6 = self.relu(self.fc6(h5))
    return h6.view(input.shape)

As a reminder, the rule for convolutions is: with kernel $k$, padding $p$, and stride $s$, an $i \times i$ input will have side length $(i+2p-k)/s+1$.

In [ ]:
class ConvHarmonizer(nn.Module):
  def __init__(self):
    super(ConvHarmonizer, self).__init__()
    # size is batch_size x 70 x 96
    self.main = nn.Sequential(
        nn.Conv2d(1, 32, 10, 2, 2),
        nn.ReLU(True),
        # shape is 64 x 33 x 46 
        nn.Conv2d(32, 64, 8, 1, 2),
        nn.ReLU(True),
        # shape is 128 x 30 x 43,
        nn.Conv2d(64, 128, 8, 1, 2),
        nn.ReLU(True),
        # shape is 128 x 27 x 40
        nn.ConvTranspose2d(128, 64, 8, 1, 2),
        nn.ReLU(True),
        nn.ConvTranspose2d(64, 32, 8, 1, 2),
        nn.ReLU(True),
        nn.ConvTranspose2d(32, 1, 10, 2, 2),
        nn.ReLU(True)
    )

  def forward(self, x):
    return self.main(x.unsqueeze(1)).squeeze(1)

In [ ]:
def trainHarmonizer(epochs=30, rate=1e-6, conv=False):
  if conv:
    model = ConvHarmonizer()
  else:
    model = Harmonizer()
  model.to(device)

  # Define Loss, Optimizer
  criterion = nn.MSELoss()
  optimizer = torch.optim.Adam(model.parameters(), lr=rate)

  epoch_times = []
  phases = ['val', 'train']
  best_loss = 1e6

  for epoch in range(1, epochs + 1):
    losses = []
    for phase in phases:
      if phase == 'train':
        model.train()
        loader = train_loader
      else:
        model.eval()
        loader = test_loader

      start_time = time.clock()
      counter = 0
      running_loss = 0
      for i, o in loader:
        # if i.size(0) and conv != 32:
        #   pass
        i = i.to(device)
        o = o.to(device)
        counter += 1
        optimizer.zero_grad()
        out = model(i.float())
        loss = criterion(out, o)
        if phase == 'train':
          loss.backward()
          optimizer.step()
        running_loss += loss.item() * i.size(0)

      epoch_loss = running_loss / len(loader.dataset)
      losses.append(epoch_loss)
      if phase == 'val':
          if best_loss > epoch_loss:
              best_loss = min(epoch_loss, best_loss)
              best_model_wts = copy.deepcopy(model.state_dict())

    current_time = time.clock()
    elapsed = current_time-start_time
    print("_"*60)
    print("Completed epoch {} of {} in {:.4f} seconds".format(epoch, epochs, elapsed))
    print("Train Loss: {:.4f}.....Validation Loss: {:.4f}" \
          .format(losses[0], losses[1]))
    epoch_times.append(elapsed)

  print("Total Training Time: {:4f} seconds".format(sum(epoch_times)))
  model.load_state_dict(best_model_wts)
  return model

In [ ]:
model = trainHarmonizer(epochs=25)

____________________________________________________________
Completed epoch 1 of 25 in 12.9781 seconds
Train Loss: 0.0146.....Validation Loss: 0.0139
____________________________________________________________
Completed epoch 2 of 25 in 12.9924 seconds
Train Loss: 0.0132.....Validation Loss: 0.0135
____________________________________________________________
Completed epoch 3 of 25 in 12.9307 seconds
Train Loss: 0.0130.....Validation Loss: 0.0132
____________________________________________________________
Completed epoch 4 of 25 in 13.0024 seconds
Train Loss: 0.0128.....Validation Loss: 0.0130
____________________________________________________________
Completed epoch 5 of 25 in 12.9253 seconds
Train Loss: 0.0126.....Validation Loss: 0.0127
____________________________________________________________
Completed epoch 6 of 25 in 12.9415 seconds
Train Loss: 0.0123.....Validation Loss: 0.0124
____________________________________________________________
Completed epoch 7 of 25 in 12.950

This looks pretty promising to me! What I like best is that the validation loss goes down with the training loss, even though they contain a different set of pieces. But of course, we have to listen to really hear what the network does.

In [ ]:
from pypianoroll import write, parse, Track, Multitrack
import IPython.display as ipd

def play(np_clipped):
  ''' wraps np roll to full 128 pitch proll, writes to midi, 
      synthesize the midi to audio, and then play it '''
  proll = np.zeros((128, 96))
  proll[20:90,:] = np_clipped
  try:
    write(Multitrack(tracks=[Track(proll.T)], beat_resolution=8), 'file.mid')
    mid = pretty_midi.PrettyMIDI('file.mid')
    audio = mid.synthesize()
    ipd.display(ipd.Audio(audio, rate=44100))
  except Exception as e:
    print('failed :o :/ with error: ', e)

def listen_to_outputs(m, inds = [10,11,12]):
  ''' plays model m output and true output one after another.
      takes tensor output, converts to binarized np array,
      and then writes to midi before displaying audio '''
  for ind in inds:
    i, o = next(iter(train_loader))
    all_outs = m(i.to(device).float())[ind]
    out = all_outs.cpu().detach().numpy()
    out = 1. * (out > 0.05)
    col_max_inds = np.argmax(out, axis=0)
    out[col_max_inds, np.arange(out.shape[1])] = 1
    out[out < 1] = 0
    tr = o[ind].numpy()
    print('Model Output')
    play(out)
    print('True Output')
    play(tr)
    print('_'*20)

listen_to_outputs(model)

Model Output


True Output


____________________
Model Output


True Output


____________________
Model Output


True Output


____________________


In [ ]:
conv_model = trainHarmonizer(conv=True)

____________________________________________________________
Completed epoch 1 of 30 in 22.0635 seconds
Train Loss: 0.1198.....Validation Loss: 0.0211
____________________________________________________________
Completed epoch 2 of 30 in 22.0241 seconds
Train Loss: 0.0116.....Validation Loss: 0.0105
____________________________________________________________
Completed epoch 3 of 30 in 22.0564 seconds
Train Loss: 0.0095.....Validation Loss: 0.0091
____________________________________________________________
Completed epoch 4 of 30 in 22.2926 seconds
Train Loss: 0.0085.....Validation Loss: 0.0084
____________________________________________________________
Completed epoch 5 of 30 in 21.9189 seconds
Train Loss: 0.0080.....Validation Loss: 0.0079
____________________________________________________________
Completed epoch 6 of 30 in 22.0506 seconds
Train Loss: 0.0077.....Validation Loss: 0.0077
____________________________________________________________
Completed epoch 7 of 30 in 22.078

In [ ]:
listen_to_outputs(conv_model)

Model Output


True Output


____________________
Model Output


True Output


____________________
Model Output


True Output


____________________


The convolutional model seems to learn the notes, though it also has some spurious incorrect notes. Also, some held notes become interrupted, which really hurts the sound quality, but all in all, I do think that the simple model worked well in learning the harmonizations. 

In [ ]:
t = torch.rand((4,3))
print(t)
print(t.argmax(dim=0))
print(torch.max(t, dim=0))
z = torch.zeros_like(t)
inds = torch.max(t, dim=0)[1]
inds2 = torch.stack((inds, torch.arange(t.shape[1])))
print(inds2)
z[inds2] = 1
print(z)

tensor([[0.5325, 0.2510, 0.0889],
        [0.7942, 0.4825, 0.9633],
        [0.6599, 0.1767, 0.6481],
        [0.6150, 0.3459, 0.2512]])
tensor([1, 1, 1])
torch.return_types.max(
values=tensor([0.7942, 0.4825, 0.9633]),
indices=tensor([1, 1, 1]))
tensor([[1, 1, 1],
        [0, 1, 2]])
tensor([[1., 1., 1.],
        [1., 1., 1.],
        [1., 1., 1.],
        [0., 0., 0.]])


In [ ]:
y = np.random.randn(4,3)
print(y)
print(np.argmax(y, axis=0))
col_max_inds = np.argmax(y, axis=0)
max_tuple_inds = [(i,x) for x,i in enumerate(col_max_inds)]
print(max_tuple_inds)
# y[[max_tuple_inds]]=1
y[col_max_inds, np.arange(y.shape[1])] = 1
print(y)

[[-0.82862084  1.58792934  1.31573515]
 [-0.1475584  -1.56784535  1.08335796]
 [-1.1133637   0.44543506 -0.16001584]
 [-0.38336761  0.0705643  -0.57730674]]
[1 0 0]
[(1, 0), (0, 1), (0, 2)]
[[-0.82862084  1.          1.        ]
 [ 1.         -1.56784535  1.08335796]
 [-1.1133637   0.44543506 -0.16001584]
 [-0.38336761  0.0705643  -0.57730674]]


In [ ]:
w = [(i.item(),x) for x,i in enumerate(inds)]
print(w)
z = torch.zeros_like(t)
print(z)
z[w] = 1
print(z)

[(0, 0), (3, 1), (0, 2)]
tensor([[0., 0., 0.],
        [0., 0., 0.],
        [0., 0., 0.],
        [0., 0., 0.]])


IndexError: ignored